In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/arabic-history-questions-dataset/all_data_flattened.json
/kaggle/input/arabic-history-questions-dataset/all_data.json
/kaggle/input/arabic-history-questions-dataset/train.json
/kaggle/input/arabic-history-questions-dataset/test.json
/kaggle/input/arabic-history-questions-dataset/test_raw.json
/kaggle/input/arabic-history-questions-dataset/val_raw.json
/kaggle/input/arabic-history-questions-dataset/train_raw.json
/kaggle/input/arabic-history-questions-dataset/val.json
/kaggle/input/finetuned_qg_arat5/transformers/default/6/__huggingface_repos__.json
/kaggle/input/finetuned_qg_arat5/transformers/default/6/arat5_qg/final_model/config.json
/kaggle/input/finetuned_qg_arat5/transformers/default/6/arat5_qg/final_model/spiece.model
/kaggle/input/finetuned_qg_arat5/transformers/default/6/arat5_qg/final_model/training_args.bin
/kaggle/input/finetuned_qg_arat5/transformers/default/6/arat5_qg/final_model/tokenizer.json
/kaggle/input/finetuned_qg_arat5/transformers/default/6/arat5_qg/

In [2]:
#Custom Dataset finetune
model_path = "/kaggle/input/finetuned_qg_arat5/transformers/default/6/finetuned-AraT5-QG/checkpoint-1036"

# #Arasquad Datast finetune
# model_path = "/kaggle/input/qgarabicsquad-finetuned/transformers/default/1/arat5_finetuned/final_model"

print("Files in model directory:", os.listdir(model_path))

Files in model directory: ['config.json', 'trainer_state.json', 'spiece.model', 'training_args.bin', 'tokenizer.json', 'tokenizer_config.json', 'scaler.pt', 'scheduler.pt', 'model.safetensors', 'special_tokens_map.json', 'optimizer.pt', 'rng_state.pth', 'generation_config.json']


In [3]:
from transformers import AutoTokenizer, AutoModelForSeq2SeqLM

# Load tokenizer with custom special tokens
tokenizer = AutoTokenizer.from_pretrained(
    model_path,
    use_fast=True  # Required for SentencePiece (spiece.model)
)

# Load model
model = AutoModelForSeq2SeqLM.from_pretrained(model_path)

2025-06-20 18:50:17.468351: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1750445417.706167      19 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1750445417.779989      19 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered


In [4]:
print(tokenizer.special_tokens_map)
# Should show:
# {'additional_special_tokens': ['<context>', '<answer>', '<question>'], ...}

{'eos_token': '</s>', 'unk_token': '<unk>', 'pad_token': '<pad>', 'additional_special_tokens': ['<extra_id_0>', '<extra_id_1>', '<extra_id_2>', '<extra_id_3>', '<extra_id_4>', '<extra_id_5>', '<extra_id_6>', '<extra_id_7>', '<extra_id_8>', '<extra_id_9>', '<extra_id_10>', '<extra_id_11>', '<extra_id_12>', '<extra_id_13>', '<extra_id_14>', '<extra_id_15>', '<extra_id_16>', '<extra_id_17>', '<extra_id_18>', '<extra_id_19>', '<extra_id_20>', '<extra_id_21>', '<extra_id_22>', '<extra_id_23>', '<extra_id_24>', '<extra_id_25>', '<extra_id_26>', '<extra_id_27>', '<extra_id_28>', '<extra_id_29>', '<extra_id_30>', '<extra_id_31>', '<extra_id_32>', '<extra_id_33>', '<extra_id_34>', '<extra_id_35>', '<extra_id_36>', '<extra_id_37>', '<extra_id_38>', '<extra_id_39>', '<extra_id_40>', '<extra_id_41>', '<extra_id_42>', '<extra_id_43>', '<extra_id_44>', '<extra_id_45>', '<extra_id_46>', '<extra_id_47>', '<extra_id_48>', '<extra_id_49>', '<extra_id_50>', '<extra_id_51>', '<extra_id_52>', '<extra_id_53

In [5]:
!pip install -qU json-repair==0.29.1

In [6]:
import json
from json_repair import json_repair

In [7]:
import json_repair
def parse_json(text):
    try:
        return json_repair.loads(text)
    except:
        return None

In [8]:
import json
import json_repair
from collections import Counter

# Function to parse and repair JSON
def parse_json(file_path):
    with open(file_path, "r", encoding="utf-8") as file:
        text = file.read()
    try:
        return json_repair.loads(text)  # Repair and parse JSON
    except Exception as e:
        print(f"خطأ في تحليل JSON: {e}")
        return None

# Step 1: Count the number of questions per paragraph
def get_question_count_frequency(data):
    question_counts = [len(item.get("questions", [])) for item in data]
    return Counter(question_counts)

# Step 2: Filter paragraphs with 5 or more questions and trim to exactly 5
def filter_paragraphs_with_five_questions(data):
    filtered = []
    for item in data:
        questions = item.get("questions", [])
        if len(questions) >= 5:
            item["questions"] = questions[:5]  # Keep only the first 5
            filtered.append(item)
    return filtered

# Step 3: Remove duplicate paragraphs based on paragraph content
def remove_duplicate_paragraphs(data):
    seen_paragraphs = set()
    unique_data = []
    for item in data:
        paragraph = item.get("paragraph", "")
        if paragraph not in seen_paragraphs:
            seen_paragraphs.add(paragraph)
            unique_data.append(item)
    return unique_data

# --- Main Execution ---
file_path = "/kaggle/input/arabic-history-questions-dataset/test_raw.json"
data = parse_json(file_path)

if data:
    # Step 1: Get frequency of question counts
    count_freq = get_question_count_frequency(data)
    print("توزيع عدد الأسئلة في الفقرات:", count_freq)

    # Step 2: Filter dataset to include only paragraphs with exactly 5 questions
    filtered_data = filter_paragraphs_with_five_questions(data)
    print(f"\nعدد الفقرات بعد التصفية: {len(filtered_data)}")

    # Step 3: Remove duplicate paragraphs
    unique_data = remove_duplicate_paragraphs(filtered_data)
    print(f"\nعدد الفقرات بعد إزالة التكرار: {len(unique_data)}")

    # Step 4: Save filtered and unique dataset
    with open("paragraphs_with_5_questions_unique.json", "w", encoding="utf-8") as f:
        json.dump(unique_data, f, indent=2, ensure_ascii=False)

    print("تم إنشاء ملف يحتوي على الفقرات التي تحتوي على 5 أسئلة فقط، بدون تكرار.")
else:
    print("فشل في تحميل بيانات JSON.")


توزيع عدد الأسئلة في الفقرات: Counter({6: 20, 7: 17, 5: 17, 8: 17, 10: 12, 9: 8, 15: 2})

عدد الفقرات بعد التصفية: 93

عدد الفقرات بعد إزالة التكرار: 93
تم إنشاء ملف يحتوي على الفقرات التي تحتوي على 5 أسئلة فقط، بدون تكرار.


In [9]:
len(unique_data)

93

In [10]:
# Convert to DataFrame
df = pd.DataFrame(unique_data)

# Display the DataFrame
df.head()

paragraph  \
0  أصدر العثمانيون كتيبات بهدف الدعوة إلى الجهاد ...   
1  العلوم الإنسانية والاجتماعية: برع المسلمون فى ...   
2  أدت المسيرة الحتمية إلى الحرب الأهلية والقتال ...   
3  من أبرز تأثيرات العصر العباسي أيضًا؛ ظهور وتطو...   
4  ٧ـ الصناعات الحجرية: تعد من أقدم الصناعات التى...   

                                          topic  \
0             التواصل بين الشريف حسين وبريطانيا   
1                 إنجازات المسلمين في الجغرافيا   
2  الحرب الأهلية الإسبانية وتأثيرها على فالنسيا   
3  المذاهب الفقهية وجمع الحديث في العصر العباسي   
4               الصناعات الحجرية في مصر القديمة   

                                           questions  
0  [{'question': 'ما هو الهدف الأساسي من إصدار ال...  
1  [{'question': 'ما هي إحدى إنجازات المسلمين في ...  
2  [{'question': 'متى أصبحت فالنسيا عاصمة الجمهور...  
3  [{'question': 'ما هي المدارس الفقهية الأربعة ا...  
4  [{'question': 'ما هي الصناعة التي تعد من أقدم ...

In [11]:
df = df.sample(frac=1, random_state=42).reset_index(drop=True)
df.head()

paragraph  \
0  هـ- الرياضيات: الجبر: أسس العالم الإسلامي الخو...   
1  الألعاب الرياضية: احتلت الألعاب الرياضية مكانه...   
2  مجىء الحملة الفرنسية إلى مصر رغم أن الاحتلال ا...   
3  أدوات الزينة: كان المصريون القدماء يعتنون بالن...   
4  أصدر العثمانيون كتيبات بهدف الدعوة إلى الجهاد ...   

                               topic  \
0                   الرياضيات: الجبر   
1      رياضة المصارعة في مصر القديمة   
2            الحملة الفرنسية على مصر   
3              أدوات الزينة والتجميل   
4  التواصل بين الشريف حسين وبريطانيا   

                                           questions  
0  [{'question': 'من هو العالم الذي أسس علم الجبر...  
1  [{'question': 'ما هي الرياضة التي اهتم بها أبن...  
2  [{'question': 'ما السبب الرئيسي في قدوم الحملة...  
3  [{'question': 'ما هي المواد التي كانت تُستخدم ...  
4  [{'question': 'ما هو الهدف الأساسي من إصدار ال...

In [12]:
# df = df.iloc[:87]
df.rename(columns={"paragraph": "context"}, inplace=True)

df.head()

context  \
0  هـ- الرياضيات: الجبر: أسس العالم الإسلامي الخو...   
1  الألعاب الرياضية: احتلت الألعاب الرياضية مكانه...   
2  مجىء الحملة الفرنسية إلى مصر رغم أن الاحتلال ا...   
3  أدوات الزينة: كان المصريون القدماء يعتنون بالن...   
4  أصدر العثمانيون كتيبات بهدف الدعوة إلى الجهاد ...   

                               topic  \
0                   الرياضيات: الجبر   
1      رياضة المصارعة في مصر القديمة   
2            الحملة الفرنسية على مصر   
3              أدوات الزينة والتجميل   
4  التواصل بين الشريف حسين وبريطانيا   

                                           questions  
0  [{'question': 'من هو العالم الذي أسس علم الجبر...  
1  [{'question': 'ما هي الرياضة التي اهتم بها أبن...  
2  [{'question': 'ما السبب الرئيسي في قدوم الحملة...  
3  [{'question': 'ما هي المواد التي كانت تُستخدم ...  
4  [{'question': 'ما هو الهدف الأساسي من إصدار ال...

In [13]:
# Show column names
print(df.columns)

Index(['context', 'topic', 'questions'], dtype='object')


In [14]:
df.drop(columns=['topic'], inplace=True)

In [15]:
print(df.columns)

Index(['context', 'questions'], dtype='object')


In [16]:
df['questions'].iloc[0]


[{'question': 'من هو العالم الذي أسس علم الجبر؟',
  'options': ['الخوارزمي',
   'أبو كامل شجاع المصري',
   'عمر الخيام',
   'لا يمكن تحديدها من النص'],
  'correct_answer': 'الخوارزمي',
  'tags': ['الخوارزمي', 'علم الجبر'],
  'difficulty': 'سهل',
  'bloom_taxonomy': 'Remembering'},
 {'question': 'ما هو الغرض الذي ابتكر من أجله الخوارزمي علم الجبر؟',
  'options': ['حل بعض المسائل الصعبة فى قضايا الميراث',
   'تطوير العلوم الرياضية',
   'إدخال الصفر في الترقيم',
   'لا يمكن تحديدها من النص'],
  'correct_answer': 'حل بعض المسائل الصعبة فى قضايا الميراث',
  'tags': ['الخوارزمي', 'قضايا الميراث'],
  'difficulty': 'سهل',
  'bloom_taxonomy': 'Remembering'},
 {'question': 'ما هو الابتكار الذي قام به العلماء المسلمون في الترقيم؟',
  'options': ['إدخال الصفر في الترقيم',
   'استخدام الأرقام الرومانية',
   'استخدام الأرقام العربية',
   'لا يمكن تحديدها من النص'],
  'correct_answer': 'إدخال الصفر في الترقيم',
  'tags': ['إدخال الصفر في الترقيم', 'العلماء المسلمون'],
  'difficulty': 'سهل',
  'bloom_

In [17]:
df['questions'] = df['questions'].apply(lambda qs: [q['question'] for q in qs])


In [18]:
print(df['questions'].iloc[0])

['من هو العالم الذي أسس علم الجبر؟', 'ما هو الغرض الذي ابتكر من أجله الخوارزمي علم الجبر؟', 'ما هو الابتكار الذي قام به العلماء المسلمون في الترقيم؟', 'ما الذي ترتب على إدخال الصفر في الترقيم؟', 'من هم العلماء الذين ساهموا في تطوير علم الجبر؟']


In [19]:
df.head()

context  \
0  هـ- الرياضيات: الجبر: أسس العالم الإسلامي الخو...   
1  الألعاب الرياضية: احتلت الألعاب الرياضية مكانه...   
2  مجىء الحملة الفرنسية إلى مصر رغم أن الاحتلال ا...   
3  أدوات الزينة: كان المصريون القدماء يعتنون بالن...   
4  أصدر العثمانيون كتيبات بهدف الدعوة إلى الجهاد ...   

                                           questions  
0  [من هو العالم الذي أسس علم الجبر؟, ما هو الغرض...  
1  [ما هي الرياضة التي اهتم بها أبناء الملوك والأ...  
2  [ما السبب الرئيسي في قدوم الحملة الفرنسية إلى ...  
3  [ما هي المواد التي كانت تُستخدم في صناعة الخوا...  
4  [ما هو الهدف الأساسي من إصدار العثمانيين كتيبا...

In [20]:
# !pip install -qU transformers==4.48.3 datasets==3.2.0 optimum==1.24.0


In [21]:
len(df)

93

In [23]:
def generate_questions(context, num_questions=3):
    """
    Generates multiple diverse questions from a given context.

    Args:
        context (str): The input text or paragraph.
        num_questions (int): Number of diverse questions to generate.

    Returns:
        list: A list of generated questions.
    """
    # Format the prompt if you're using a model trained with a specific format
    input_text = f"{context}"
    #input_text=context
    # Tokenize input
    inputs = tokenizer(
        input_text,
        return_tensors="pt",
        max_length=512,
        truncation=True,
        padding="max_length"
    ).to(model.device)

    # Generate multiple questions
    outputs = model.generate(
    input_ids=inputs["input_ids"],
    attention_mask=inputs["attention_mask"],
    do_sample=False,
    temperature=0.9,
    num_beams=6,
    num_beam_groups=3,  # 6 / 3 = 2 beams per group
    diversity_penalty=1.0,
    num_return_sequences=3
    )

    # Decode and clean
    questions = []
    for output in outputs:
        question = tokenizer.decode(output, skip_special_tokens=True).replace("<question>", "").strip()
        questions.append(question)
    return questions


In [24]:
# context = "تم تولية محمد على حكم مصر بإرادة الشعب المصرى، رغم اعتراض الباب العالى العثمانى، فسعى نحو جعل نقطة الارتكاز له ولأبنائه من بعده فى مصر لا فى الآستانة، وقد نجح فى فترة وجيزة فى جعل ولايته (مصر) أكثر حضارة وتقدمًا من الدولة العثمانية صاحبة السيادة؛ فكان من الطبيعى أن تستقل عنها. ولكن محمد على أراد أن يحمى هذا الاستقلال ويحيطه بسياج من الحدود الطبيعية فى الشام شرقًا والسودان جنوبًا، وبدأت من هنا سياسة (محمد على) الخارجية وتحركاته التوسعية لحماية الحدود المصرىة."
context = "العلوم الإنسانية والاجتماعية: برع المسلمون فى كثير من العلوم الإنسانية والاجتماعية التى وضعوا الأسس التى قامت على ضوئها النظريات وتطورت العلوم بعد ذلك. من إنجازات المسلمين في الجغرافيا:- رسم خطوط الطول ودوائر العرض: يعدُّ المسلمون أول من وضع خطوط الطول ودوائر العرض على خريطة الكرة الأرضية وضعها العالم أبو علي المراكشي (ت 660هـ - 1262م) وذلك لكى يستدل المسلمون على الساعات المتساوية فى بقاع الأرض المختلفة للصلاة.. كما وضع البيروني قاعدة حسابية لتسطيح الكرة أي نقل الخطوط والخرائط من الكرة إلى سطح مسطح وبالعكس.. وبهذا سهل رسم الخرائط الجغرافية."
questions = generate_questions(context, 5)

for i, q in enumerate(questions, 1):
    print(f"Question {i}: {q}")

/usr/local/lib/python3.11/dist-packages/transformers/generation/configuration_utils.py:631: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.9` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`.
  warnings.warn(


Question 1: ما هو الهدف من وضع خطوط الطول ودوائر العرض على خريطة الكرة الأرضية؟
Question 2: ما هي إحدى إنجازات المسلمين في الجغرافيا؟
Question 3: ما هو الدور الذي لعبه المسلمون في تطور العلوم؟


In [25]:
# # Check your test dataset has both input and target
# print(tokenized_qg_datasets["test"][0])

In [26]:
# # Decode the input (context)
# input_text = tokenizer.decode(tokenized_qg_datasets["test"][0]["input_ids"])
# print("Decoded Input:", input_text)

# # Decode the labels (target question)
# # Note: Need to filter out -100 values (padding) first
# labels = [x for x in tokenized_qg_datasets["test"][0]["labels"] if x != -100]
# label_text = tokenizer.decode(labels)
# print("Decoded Label:", label_text)

In [27]:
# print("\nDataset features:", tokenized_qg_datasets["test"].features)

In [28]:
# for i in range(3):  # First 3 examples
#     print(f"\nExample {i}:")
#     input_text = tokenizer.decode(
#         [x for x in tokenized_qg_datasets["test"][i]["input_ids"] if x != tokenizer.pad_token_id]
#     )
#     label_text = tokenizer.decode(
#         [x for x in tokenized_qg_datasets["test"][i]["labels"] if x != -100]
#     )
#     print("Input:", input_text)
#     print("Label:", label_text)

In [29]:
!pip install evaluate


huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 84.1/84.1 kB 3.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 193.6/193.6 kB 10.3 MB/s eta 0:00:00
  Attempting uninstall: fsspec
    Found existing installation: fsspec 2025.3.2
    Uninstalling fsspec-2025.3.2:
      Successfully uninstalled fsspec-2025.3.2
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
cesium 0.12.4 requires numpy<3.0,>=2.0, but you have numpy 1.26.4 which is incompatible.
bigframes 1.42.0 requires rich<14,>=12.4.4, but you have rich 14.0.0 which is incompatible.
torch 2.6.0+cu124 requires nvidia-cublas-cu12==12.4.5.8; platform_system == "Linux" and platform_machine == "x86_64", but you have nvidia-cublas-cu12 12.9.0.13 which is incompatible.
torch 2.6.0+cu124 requires nvidia-cudnn-cu12==9.1.0.70; platform_system == "Linux" and platform_machine == "x86_64", but you have nvidia-cudn

In [30]:
# !pip install -U transformers evaluate

In [31]:
!pip install rouge-score nltk pandas tqdm
!python -m nltk.downloader punkt
!pip install evaluate rouge-score

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


  Preparing metadata (setup.py) ... done
  Created wheel for rouge-score: filename=rouge_score-0.1.2-py3-none-any.whl size=24934 sha256=082eb9eaf71cb8c4c067a87b10e0065e633faa824dfe47ffbff21531d0f7f9f5
  Stored in directory: /root/.cache/pip/wheels/1e/19/43/8a442dc83660ca25e163e1bd1f89919284ab0d0c1475475148
Successfully built rouge-score


huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


<frozen runpy>:128: RuntimeWarning: 'nltk.downloader' found in sys.modules after import of package 'nltk', but prior to execution of 'nltk.downloader'; this may result in unpredictable behaviour
[nltk_data] Downloading package punkt to /usr/share/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


In [32]:
# !pip install -U evaluate


In [33]:
# !pip uninstall -y evaluate rouge_score
# !rm -rf ~/.cache/huggingface/modules/evaluate_modules


In [34]:
# !pip install evaluate==0.4.0 rouge_score


# **BERTScore**

In [35]:
!pip install bert-score

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 61.1/61.1 kB 3.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 4.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 2.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 6.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 31.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 13.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 2.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 80.2 MB/s eta 0:00:00
  Attempting uninstall: nvidia-nvjitlink-cu12
    Found existing installation: nvidia-nvjitlink-cu12 12.9.41
    Uninstalling nvidia-nvjitlink-cu12-12.9.41:
      Successfully uninstalled nvidia-nvjitlink-cu12-12.9.41
  Attempting uninstall: nvidia-curand-cu12
    Found existing installation: nvidia-curand-cu12 10.3.10.19
    Uninstalling nvidia-curand-cu12-10.

In [36]:
from sentence_transformers import SentenceTransformer, util
# Load a multilingual embedding model for similarity comparison
embedder = SentenceTransformer('akhooli/Arabic-SBERT-100K')


modules.json:   0%|          | 0.00/229 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/195 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/17.6k [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/53.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/637 [00:00<?, ?B/s]

...

tokenizer_config.json:   0%|          | 0.00/1.82k [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/761k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.78M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/695 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/296 [00:00<?, ?B/s]

In [38]:
from bert_score import score as bert_score
import torch

def evaluate_qg_from_df_bert_reference(df, generate_questions, num_samples=100, num_questions=3):
    results = []
    paragraph_scores = []

    for i, row in df.iterrows():
        if i == num_samples:
            break

        context = row['context']
        reference_questions = row['questions']  # List of strings

        # print(f"\n\n=== Sample {i+1} ===")
        # print(f"Context: {context[:200]}...")
        # print(f"Reference Questions ({len(reference_questions)}): {reference_questions}")

        # Generate new questions
        generated_questions = generate_questions(context, num_questions=num_questions)
        # print("\nGenerated Questions:")
        # for j, q in enumerate(generated_questions, 1):
        #     print(f"  G{j}: {q}")

        # Compute embeddings
        ref_embeddings = embedder.encode(reference_questions, convert_to_tensor=True)
        gen_embeddings = embedder.encode(generated_questions, convert_to_tensor=True)

        best_pair = None
        best_score = -1

        for g_idx, gen_emb in enumerate(gen_embeddings):
            cos_scores = util.pytorch_cos_sim(gen_emb, ref_embeddings)[0]
            max_idx = torch.argmax(cos_scores).item()
            max_score = cos_scores[max_idx].item()

            if max_score > best_score:
                best_score = max_score
                best_pair = (generated_questions[g_idx], reference_questions[max_idx])

        if best_pair:
            gq, rq = best_pair
            # print(f"\n→ Best Matching Pair:")
            # print(f"  Generated: \"{gq}\"")
            # print(f"  Reference: \"{rq}\"")
            P, R, F1 = bert_score([gq], [rq], lang="ar")
            score_value = F1[0].item()
            # print(f"  → BERTScore: {score_value:.5f}")

            paragraph_scores.append(score_value)
            results.append({
                "sample": i + 1,
                "generated_question": gq,
                "matched_reference": rq,
                "bert_score": score_value,
            })

    # Compute average BERTScore
    if paragraph_scores:
        avg_score = sum(paragraph_scores) / len(paragraph_scores)
        print(f"\n📊 Average BERTScore (refernce)across {len(paragraph_scores)} paragraphs: {avg_score:.5f}")
    else:
        print("⚠️ No scores calculated.")

    return results

results = evaluate_qg_from_df_bert_reference(df,
                              generate_questions, 
                              num_samples=93,
                              num_questions=3)


/usr/local/lib/python3.11/dist-packages/transformers/generation/configuration_utils.py:631: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.9` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`.
  warnings.warn(


Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

tokenizer_config.json:   0%|          | 0.00/49.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/625 [00:00<?, ?B/s]

...

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]


📊 Average BERTScore (refernce)across 93 paragraphs: 0.86878


# F1-SCORE

In [42]:
import torch
import re
from sklearn.metrics import precision_score, recall_score, accuracy_score

def simple_token_f1_reference(prediction, reference):
    pred_tokens = re.findall(r'\w+', prediction)
    ref_tokens = re.findall(r'\w+', reference)
    common = set(pred_tokens) & set(ref_tokens)

    overlap = len(common)
    if len(pred_tokens) == 0 or len(ref_tokens) == 0 or overlap == 0:
        return 0.0, 0.0, 0.0  # F1, Precision, Recall

    precision = overlap / len(pred_tokens)
    recall = overlap / len(ref_tokens)
    f1 = 2 * precision * recall / (precision + recall)
    
    return f1, precision, recall

def evaluate_qg_from_df_f1_reference(df, generate_questions, num_samples=100, num_questions=3):
    results = []
    paragraph_scores = []
    all_true_labels = []
    all_pred_labels = []

    for i, row in df.iterrows():
        if i == num_samples:
            break

        context = row['context']
        reference_questions = row['questions']  # List of strings

        # print(f"\n\n=== Sample {i+1} ===")
        # print(f"Context: {context[:200]}...")
        # print(f"Reference Questions ({len(reference_questions)}): {reference_questions}")

        # Generate new questions
        generated_questions = generate_questions(context, num_questions=num_questions)
        # print("\nGenerated Questions:")
        # for j, q in enumerate(generated_questions, 1):
        #     print(f"  G{j}: {q}")

        # Compute embeddings
        ref_embeddings = embedder.encode(reference_questions, convert_to_tensor=True)
        gen_embeddings = embedder.encode(generated_questions, convert_to_tensor=True)

        best_pair = None
        best_score = -1

        for g_idx, gen_emb in enumerate(gen_embeddings):
            gq = generated_questions[g_idx]
            cos_scores = util.pytorch_cos_sim(gen_emb, ref_embeddings)[0]

            # print(f"\n🔍 Similarities for Generated Question {g_idx + 1}: \"{gq}\"")
            # for r_idx, score in enumerate(cos_scores):
            #     rq = reference_questions[r_idx]
            #     print(f"  → Ref {r_idx + 1}: \"{rq}\" → Score: {score.item():.4f}")

            max_idx = torch.argmax(cos_scores).item()
            max_score = cos_scores[max_idx].item()

            if max_score > best_score:
                best_score = max_score
                best_pair = (gq, reference_questions[max_idx])

        if best_pair:
            gq, rq = best_pair
            # print(f"\n✅ Best Matching Pair:")
            # print(f"  Generated: \"{gq}\"")
            # print(f"  Reference: \"{rq}\"")
            f1, precision, recall = simple_token_f1_reference(gq, rq)
            # print(f"  → F1 Score: {f1:.5f}, Precision: {precision:.5f}, Recall: {recall:.5f}")

            paragraph_scores.append(f1)
            results.append({
                "sample": i + 1,
                "generated_question": gq,
                "matched_reference": rq,
                "f1_score": f1,
                "precision": precision,
                "recall": recall,
            })
            all_true_labels.append(rq)
            all_pred_labels.append(gq)

    if paragraph_scores:
        avg_f1 = sum(paragraph_scores) / len(paragraph_scores)
        avg_precision = sum([result["precision"] for result in results]) / len(results)
        avg_recall = sum([result["recall"] for result in results]) / len(results)

        # Calculate accuracy based on exact match (for simplicity, we assume exact match is accurate)
        accuracy = accuracy_score(all_true_labels, all_pred_labels)

        print(f"\n📊 Average Scores(reference) across {len(paragraph_scores)} paragraphs:")
        print(f"   Average F1 Score: {avg_f1:.5f}")
        print(f"   Average Precision: {avg_precision:.5f}")
        print(f"   Average Recall: {avg_recall:.5f}")
        print(f"   Accuracy: {accuracy:.5f}")
    else:
        print("⚠️ No scores calculated.")

    return results

# Call the function to evaluate
results = evaluate_qg_from_df_f1_reference(
    df,                      # your DataFrame containing 'context' and 'questions'
    generate_questions,      # your question generation function
    num_samples=93,          # number of samples to evaluate
    num_questions=3          # number of questions to generate per context
)


Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

...

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]


📊 Average Scores(reference) across 93 paragraphs:
   Average F1 Score: 0.52109
   Average Precision: 0.51340
   Average Recall: 0.54440
   Accuracy: 0.03226


# BLEU 

In [43]:
!pip install nltk


huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


In [45]:
from nltk.translate.bleu_score import sentence_bleu, SmoothingFunction
import torch
from sentence_transformers import util

def evaluate_qg_from_df_bleu_reference(df, generate_questions, embedder, num_samples=100, num_questions=3):
    results = []
    smooth = SmoothingFunction().method1

    for i, row in df.iterrows():
        if i == num_samples:
            break

        context = row['context']
        reference_questions = row['questions']  # List of strings

        # print(f"\n\n=== Sample {i+1} ===")
        # print(f"Context: {context[:200]}...")
        # print(f"Reference Questions ({len(reference_questions)}): {reference_questions}")

        # Generate new questions
        generated_questions = generate_questions(context, num_questions=num_questions)
        # print("\nGenerated Questions:")
        # for j, q in enumerate(generated_questions, 1):
        #     print(f"  G{j}: {q}")

        # Compute embeddings for cosine similarity
        ref_embeddings = embedder.encode(reference_questions, convert_to_tensor=True)
        gen_embeddings = embedder.encode(generated_questions, convert_to_tensor=True)

        best_pair = None
        best_score = -1

        for g_idx, gen_emb in enumerate(gen_embeddings):
            gq = generated_questions[g_idx]
            cos_scores = util.pytorch_cos_sim(gen_emb, ref_embeddings)[0]

            # print(f"\n🔍 Similarities for Generated Question {g_idx + 1}: \"{gq}\"")
            # for r_idx, score in enumerate(cos_scores):
            #     rq = reference_questions[r_idx]
            #     print(f"  → Ref {r_idx + 1}: \"{rq}\" → Score: {score.item():.4f}")

            max_idx = torch.argmax(cos_scores).item()
            max_score = cos_scores[max_idx].item()

            if max_score > best_score:
                best_score = max_score
                best_pair = (generated_questions[g_idx], reference_questions[max_idx])

        if best_pair:
            gq, rq = best_pair
            # print(f"\n✅ Best Matching Pair:")
            # print(f"  Generated: \"{gq}\"")
            # print(f"  Reference: \"{rq}\"")

            # Tokenize and calculate BLEU-1, BLEU-2, BLEU-3, BLEU-4
            reference_tokens = [rq.split()]
            candidate_tokens = gq.split()

            bleu1 = sentence_bleu(reference_tokens, candidate_tokens, weights=(1, 0, 0, 0), smoothing_function=smooth)
            bleu2 = sentence_bleu(reference_tokens, candidate_tokens, weights=(0.5, 0.5, 0, 0), smoothing_function=smooth)
            bleu3 = sentence_bleu(reference_tokens, candidate_tokens, weights=(0.33, 0.33, 0.34, 0), smoothing_function=smooth)
            bleu4 = sentence_bleu(reference_tokens, candidate_tokens, weights=(0.25, 0.25, 0.25, 0.25), smoothing_function=smooth)

            # print(f"  → BLEU-1: {bleu1:.5f}")
            # print(f"  → BLEU-2: {bleu2:.5f}")
            # print(f"  → BLEU-3: {bleu3:.5f}")
            # print(f"  → BLEU-4: {bleu4:.5f}")

            results.append({
                "sample": i + 1,
                "generated_question": gq,
                "matched_reference": rq,
                "bleu_1": bleu1,
                "bleu_2": bleu2,
                "bleu_3": bleu3,
                "bleu_4": bleu4,
            })

    if results:
        avg_bleu1 = sum(r["bleu_1"] for r in results) / len(results)
        avg_bleu2 = sum(r["bleu_2"] for r in results) / len(results)
        avg_bleu3 = sum(r["bleu_3"] for r in results) / len(results)
        avg_bleu4 = sum(r["bleu_4"] for r in results) / len(results)

        print(f"\n📊 Average BLEU Scores(refernce) across {len(results)} paragraphs:")
        print(f"   BLEU-1: {avg_bleu1:.5f}")
        print(f"   BLEU-2: {avg_bleu2:.5f}")
        print(f"   BLEU-3: {avg_bleu3:.5f}")
        print(f"   BLEU-4: {avg_bleu4:.5f}")
    else:
        print("⚠️ No scores calculated.")

    return results

# Example usage:
results = evaluate_qg_from_df_bleu_reference(df,
                              generate_questions,
                              embedder,
                              num_samples=93,
                              num_questions=3)


/usr/local/lib/python3.11/dist-packages/transformers/generation/configuration_utils.py:631: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.9` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`.
  warnings.warn(


Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

...

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]


📊 Average BLEU Scores(refernce) across 93 paragraphs:
   BLEU-1: 0.45034
   BLEU-2: 0.35132
   BLEU-3: 0.27271
   BLEU-4: 0.22200


# Meteor score

In [46]:
import torch
import re
from nltk.translate.meteor_score import meteor_score
def evaluate_qg_from_df_meteor_reference(df, generate_questions, num_samples=100, num_questions=3):
    results = []
    meteor_scores = []

    for i, row in df.iterrows():
        if i == num_samples:
            break

        context = row['context']
        reference_questions = row['questions']  # List of strings

        # print(f"\n\n=== Sample {i+1} ===")
        # print(f"Context: {context[:200]}...")
        # print(f"Reference Questions ({len(reference_questions)}): {reference_questions}")

        # Generate new questions
        generated_questions = generate_questions(context, num_questions=num_questions)
        # print("\nGenerated Questions:")
        # for j, q in enumerate(generated_questions, 1):
        #     print(f"  G{j}: {q}")

        # Compute embeddings
        ref_embeddings = embedder.encode(reference_questions, convert_to_tensor=True)
        gen_embeddings = embedder.encode(generated_questions, convert_to_tensor=True)

        best_pair = None
        best_score = -1

        for g_idx, gen_emb in enumerate(gen_embeddings):
            gq = generated_questions[g_idx]
            cos_scores = util.pytorch_cos_sim(gen_emb, ref_embeddings)[0]

            # print(f"\n🔍 Similarities for Generated Question {g_idx + 1}: \"{gq}\"")
            # for r_idx, score in enumerate(cos_scores):
            #     rq = reference_questions[r_idx]
            #     print(f"  → Ref {r_idx + 1}: \"{rq}\" → Score: {score.item():.4f}")

            max_idx = torch.argmax(cos_scores).item()
            max_score = cos_scores[max_idx].item()

            if max_score > best_score:
                best_score = max_score
                best_pair = (generated_questions[g_idx], reference_questions[max_idx])

        if best_pair:
            gq, rq = best_pair
            # print(f"\n✅ Best Matching Pair:")
            # print(f"  Generated: \"{gq}\"")
            # print(f"  Reference: \"{rq}\"")

            # Tokenize for METEOR
            gq_tokens = gq.split()
            rq_tokens = rq.split()

            score = meteor_score([rq_tokens], gq_tokens)
            # print(f"  → METEOR Score: {score:.5f}")

            results.append({
                "sample": i + 1,
                "generated_question": gq,
                "matched_reference": rq,
                "meteor_score": score,
            })

            meteor_scores.append(score)

    if meteor_scores:
        avg_score = sum(meteor_scores) / len(meteor_scores)
        print(f"\n📊 Average METEOR Score(reference) across {len(meteor_scores)} paragraphs: {avg_score:.5f}")
    else:
        print("⚠️ No METEOR scores calculated.")

    return results
    
# Call the function to evaluate
results = evaluate_qg_from_df_meteor_reference(
    df,                      # your DataFrame containing 'context' and 'questions'
    generate_questions,      # your question generation function
    num_samples=93,           # number of samples to evaluate
    num_questions=3          # number of questions to generate per context
)


Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

...

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]


📊 Average METEOR Score(reference) across 93 paragraphs: 0.45977
